In [1]:
import pandas as pd
from astropy.time import Time
from pycbc import dq
import h5py
from healpy.newvisufunc import projview
import numpy as np

In [2]:
def obtime(o):
    if o == 'o1':
        s = Time('2015-09-12T00:00:00').gps
        e = Time('2016-01-19T16:00:00').gps
        hsegs = dq.query_flag('H1','DATA',s,e)
        lsegs = dq.query_flag('L1','DATA',s,e)
        return abs((hsegs & lsegs).coalesce())
    elif o=='o2':
        s = Time('2016-11-30T16:00:00').gps
        e = Time('2017-08-25T22:00:00').gps
        hsegs = dq.query_flag('H1','DATA',s,e)
        lsegs = dq.query_flag('L1','DATA',s,e)
        vsegs = dq.query_flag('V1','DATA',s,e)
    elif o=='o3a':
        s = Time('2019-04-01T15:00:00').gps
        e = Time('2019-10-01T15:00:00').gps
        hsegs = dq.query_flag('H1','DATA',s,e)
        lsegs = dq.query_flag('L1','DATA',s,e)
        vsegs = dq.query_flag('V1','DATA',s,e)
    elif o=='o3b':
        s = Time('2019-11-01T15:00:00').gps
        e = Time('2020-03-27T17:00:00').gps
        hsegs = dq.query_flag('H1','DATA',s,e)
        lsegs = dq.query_flag('L1','DATA',s,e)
        vsegs = dq.query_flag('V1','DATA',s,e)
    hlv = abs((hsegs & lsegs & vsegs).coalesce())
    hl = abs((hsegs & lsegs).coalesce()) - hlv
    lv = abs((lsegs & vsegs).coalesce()) - hlv
    hv = abs((hsegs & vsegs).coalesce()) - hlv
    return hlv + hl + lv + hv

In [3]:
for o in ['o1','o2','o3a','o3b']:
    print(o,obtime(o))

o1 4234023
o2 10557345
o3a 12923000
o3b 10765843


In [4]:
4234023/(60*60*24*364.25)

0.13453643331045528

In [5]:
df={}
for o in ['o1','o2','o3a','o3b']:
    df[o] = pd.read_csv('./search_result_'+o+'.csv')
    df[o]['false_alarm_rate'] *= (60*60*24*364.25)/obtime(o)
    print(df[o]['false_alarm_rate'])

0      14.473754
1      15.813765
2      18.862085
3      28.992894
4      38.850642
         ...    
56    616.021068
57    616.021068
58    616.021068
59    616.021068
60    616.021068
Name: false_alarm_rate, Length: 61, dtype: float64
0        0.250056
1        0.769563
2        1.349347
3        7.032599
4        9.975977
          ...    
205    647.145286
206    647.145286
207    647.145286
208    647.145286
209    647.145286
Name: false_alarm_rate, Length: 210, dtype: float64
0        0.068012
1        2.147147
2        4.410086
3        7.161301
4        9.615845
          ...    
212    551.388712
213    551.388712
214    551.388712
215    551.388712
216    551.388712
Name: false_alarm_rate, Length: 217, dtype: float64
0        1.662943
1        5.948029
2        6.346573
3        9.093370
4       11.089312
          ...    
170    570.482587
171    570.482587
172    570.482587
173    570.482587
174    570.482587
Name: false_alarm_rate, Length: 175, dtype: float64


In [6]:
frames = [df['o1'],df['o2'],df['o3a'],df['o3b']]

In [7]:
result = pd.concat(frames)

In [8]:
result.sort_values(by='false_alarm_rate',ascending=True,inplace=True)

In [9]:
result

gwname                         gwtime     gwstat       grbname  \
0    190804_185811  2019-08-04 18:58:11.868164063  11.397340  GRB190804792   
0    170331_013753  2017-03-31 01:37:53.656738281   7.601307    GRB170331A   
1    170130_071137  2017-01-30 07:11:37.379150391   7.765567  GRB170130302   
2    170306_070539  2017-03-06 07:05:39.892333984  10.279640    GRB170306A   
0    191213_060301  2019-12-13 06:03:01.360107422   6.392171  GRB191213254   
..             ...                            ...        ...           ...   
189  170428_031412  2017-04-28 03:14:12.831054687   4.248658  GRB170428136   
190  170318_120854  2017-03-18 12:08:54.047119141   2.055517    GRB170318A   
191  170317_094519  2017-03-17 09:45:19.675048828   0.368436    GRB170317A   
180  170331_013919  2017-03-31 01:39:19.490966797   4.903231    GRB170331A   
172  170208_180958  2017-02-08 18:09:58.304443359   0.642964    GRB170208A   

                           grbtime  rank_stat  false_alarm_rate  
0    2019-08-04 19:00:37.517999887  12.147027          0.068012  
0    2017-03-31 01:40:46.444639921  11.531427          0.250056  
1    2017-01-30 07:14:44.680999994  10.148487          0.769563  
2    2017-03-06 07:06:12.520600080   9.434870          1.349347  
0    2019-12-13 06:05:33.022000074   7.800304          1.662943  
..                             ...        ...               ...  
189  2017-04-28 03:16:17.457999945       -inf        647.145286  
190  2017-03-18 12:11:56.523519993       -inf        647.145286  
191  2017-03-17 09:45:59.089020014       -inf        647.145286  
180  2017-03-31 01:40:46.444639921       -inf        647.145286  
172  2017-02-08 18:11:16.327539921       -inf        647.145286  

[663 rows x 7 columns]

In [10]:
result.to_csv('merge_final_results.csv',index=False)